In [1]:
!pip install nltk
!pip install numpy
!pip install torch
!pip install torchtext
!pip install pandas
!pip install scikit-learn
!pip install tqdm
!pip uninstall jax jaxlib --yes

In [2]:
import nltk
import torch
import pickle
import random
import numpy as np
import pandas as pd
import torch.nn as nn
from tqdm import tqdm
from collections import Counter
from scipy.sparse import lil_matrix
from torch.utils.data import Dataset
from sklearn.utils.extmath import randomized_svd
from torchtext.vocab import build_vocab_from_iterator
from torch.utils.data import DataLoader, TensorDataset
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score, confusion_matrix

### Download NLTK Tokenizer

In [3]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/harshbansal/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

## Checking for Optimal Available Device

In [4]:
device = torch.device('mps' if torch.backends.mps.is_available() else 'cpu')
device

device(type='mps')

## Read Data from CSV

In [7]:
trainDataPath = "train.csv"
df = pd.read_csv(trainDataPath)
df.head()

Class Index                                        Description
0            3  Reuters - Short-sellers, Wall Street's dwindli...
1            3  Reuters - Private investment firm Carlyle Grou...
2            3  Reuters - Soaring crude prices plus worries\ab...
3            3  Reuters - Authorities have halted oil export\f...
4            3  AFP - Tearaway world oil prices, toppling reco...

In [8]:
corpus = df["Description"].apply(nltk.word_tokenize)

### Extracting 40,000 Sentences

In [9]:
corpus = corpus[:40000]

In [10]:
UNKNOWN_TOKEN = "<UNK>"

## Build Dataset and Vocabulary

In [11]:
class EntityDataset(Dataset):
    def __init__(self, data, window_size, vocabulary=None):
        """Initialize the dataset."""
        self.sentences = data
        self.window_size = window_size

        if not isinstance(data, pd.Series):
            raise TypeError("Input data must be a Pandas Series.")

        if vocabulary is not None:
            self.vocabulary = vocabulary


        word_counter = Counter()
        for sentence in data:
            for word in sentence:
                word_counter[word] += 1

        # Replace infrequent words with <UNK>
        for i, sentence in enumerate(data):
            for j, (word) in enumerate(sentence):
                if word_counter[word] < 10:  # Cutoff Frequency
                    self.sentences[i][j] = UNKNOWN_TOKEN        

        if vocabulary is None:
            self.vocabulary = build_vocab_from_iterator(self.sentences)
            self.vocabulary.set_default_index(self.vocabulary[UNKNOWN_TOKEN])

        self.index_sentences = [[self.vocabulary[word] for word in sentence] for sentence in self.sentences]
        self.index_to_word = self.vocabulary.get_itos()
        self.positive_sample, self.negative_sample, self.target_words = self.generate_sampling()

    def __len__(self):
        """Returns number of datapoints."""
        return len(self.target_words)

    def __getitem__(self, index):
        """Get the datapoint at `index`."""
        return torch.tensor(self.positive_sample[index]).to(device), torch.tensor(self.negative_sample[index]).to(device), torch.tensor(self.target_words[index]).to(device)

    def get_index_to_word(self, index):
        """Get the word corresponding to a given index."""
        return self.index_to_word[index]

    def get_word_to_index(self, word):
        """Get the word corresponding to a given index."""
        return self.vocabulary[word]

    def generate_sampling(self):
        """Sample positive and negative context words."""
        positive_sample = []
        negative_sample = []
        target_words = []
        window = self.window_size

        for sentence in tqdm(self.index_sentences, desc="Generating Positive & Negative Samples"):
            for i, target in enumerate(sentence):
                for k in range(max(0, i - window), min(len(sentence), i + window + 1)):
                    if k != i:
                        positive_sample.append(sentence[k])
                        target_words.append(target)

                        # Generate Negative Samples
                        negative_samples = []
                        while len(negative_samples) < 2 :
                            sample = random.randint(0, len(self.vocabulary) - 1)
                            if sample != target and sample not in sentence[max(0, i - window): min(len(sentence), i + window + 1)]:
                                negative_samples.append(sample)
                        negative_sample.append(negative_samples)

        return positive_sample,negative_sample, target_words

## Skip-Gram Model

In [12]:
class SkipGram(nn.Module):
    def __init__(self, vocab_size, embedding_dim=300):
        super(SkipGram, self).__init__()
        self.embedding_dim = embedding_dim
        self.context_embeddings = nn.Embedding(vocab_size, embedding_dim)
        self.target_embeddings = nn.Embedding(vocab_size, embedding_dim)

    def forward(self,positive_sample, negative_sample,target_words,learning_rate=0.01):

        target_embedding = self.target_embeddings(target_words)
        positive_embedding = self.context_embeddings(positive_sample)

        # Positive Sample
        dot_product = torch.bmm(positive_embedding.unsqueeze(1), target_embedding.unsqueeze(-1)).squeeze()
        probability = torch.sigmoid(dot_product)

        grad = (probability - 1).unsqueeze(-1) * positive_embedding
        loss = -torch.log(probability + 1e-10) 
        self.context_embeddings.weight.data[positive_sample] -= learning_rate * (probability - 1).unsqueeze(-1) * target_embedding

        num_negative_samples = negative_sample.shape[1]

        for i in range(num_negative_samples):
            reshaped_negative_sample = negative_sample[:, i:i+1]  # Reshape to (100, 1)
            embedding = self.context_embeddings(reshaped_negative_sample).squeeze(1)
            dot_product = torch.bmm(embedding.unsqueeze(1), target_embedding.unsqueeze(-1)).squeeze()
            probability = torch.sigmoid(dot_product)
            grad += (probability).unsqueeze(-1) * embedding
            loss += -torch.log(1 - probability + 1e-10) 
            self.context_embeddings.weight.data[reshaped_negative_sample.squeeze(1)] -= learning_rate * (probability).unsqueeze(-1) * target_embedding

        self.target_embeddings.weight.data[target_words] -= learning_rate * grad     

        total_loss = loss.mean() / 100
        return total_loss       

### Training the Skip-Gram Model

### Hyper-Parameters

In [13]:
context_windows = [3, 4, 5]
learning_rate = 0.1
num_epochs = 10

In [14]:
best_model = None
max_loss = 1000.0

In [13]:
for context_window in context_windows:
    dataset = EntityDataset(corpus, context_window)
    model = SkipGram(len(dataset.vocabulary), 300).to(device)


    dataloader = DataLoader(dataset, batch_size=256, shuffle=True)

    # Training loop
    for epoch in range(num_epochs):
        total_loss = 0
        predictions = []
        targets = []

        with tqdm(total=len(dataloader), desc=f'Context Window: {context_window}, Epoch {epoch+1}/{num_epochs}', unit='batch') as pbar:
            for batch, (positive_sample,negative_sample, target_words) in enumerate(dataloader):
                model.train()

                loss = model(positive_sample.to(device), negative_sample.to(device),target_words.to(device))  # Get Loss from model
                total_loss += loss.item()

                pbar.set_postfix({'loss': total_loss / (batch + 1)})
                pbar.update(1)

        print(f'Context Window: {context_window}, Epoch: {epoch+1}, Loss: {total_loss / len(dataloader):.4f}')

        average_loss = total_loss / len(dataloader)

        # Update best model 
        if average_loss < max_loss:
            max_loss = average_loss
            best_model = model

# Save the best model
torch.save(best_model, 'best_model.pt')

Context Window: 3, Epoch 1/10: 100%|██████████| 32110/32110 [12:29<00:00, 42.83batch/s, loss=0.05]


Context Window: 3, Epoch: 1, Loss: 0.0500


Context Window: 3, Epoch 2/10: 100%|██████████| 32110/32110 [12:41<00:00, 42.16batch/s, loss=0.0186]


Context Window: 3, Epoch: 2, Loss: 0.0186


Context Window: 3, Epoch 3/10: 100%|██████████| 32110/32110 [12:32<00:00, 42.66batch/s, loss=0.0132]


...

Context Window: 5, Epoch: 8, Loss: 0.0086


Context Window: 5, Epoch 9/10: 100%|██████████| 51953/51953 [20:18<00:00, 42.65batch/s, loss=0.00841]


Context Window: 5, Epoch: 9, Loss: 0.0084


Context Window: 5, Epoch 10/10: 100%|██████████| 51953/51953 [20:17<00:00, 42.68batch/s, loss=0.00828]

Context Window: 5, Epoch: 10, Loss: 0.0083


### Extracting the Embeddings

In [14]:
context_embeddings = best_model.context_embeddings.weight.data.cpu().numpy()
target_embeddings = best_model.target_embeddings.weight.data.cpu().numpy()

In [15]:
print(np.shape(context_embeddings))
print(np.shape(target_embeddings))

(10271, 300)
(10271, 300)


### Generate embeddings by Summing Context and Target Embeddings

In [16]:
word_embeddings = context_embeddings + target_embeddings

# Normalize the embeddings
word_embeddings /= np.linalg.norm(word_embeddings, axis=1, keepdims=True)
word_embeddings

array([[ 0.03290069, -0.09047558, -0.02650456, ..., -0.01732464,
        -0.10081857,  0.05301237],
       [ 0.04733349, -0.09536434, -0.01010186, ..., -0.01380922,
        -0.07548727,  0.03111346],
       [-0.0078561 , -0.05011781, -0.00989369, ..., -0.04713387,
        -0.11423495,  0.00470114],
       ...,
       [-0.00151321, -0.00382992,  0.02200773, ..., -0.06155645,
         0.09315622,  0.06318127],
       [ 0.1515942 , -0.00441719,  0.00960962, ..., -0.06585304,
         0.08873884, -0.05674504],
       [-0.11488904, -0.05626446, -0.04980468, ..., -0.03089284,
         0.05593587, -0.03656518]], dtype=float32)

In [17]:
np.shape(word_embeddings)

(10271, 300)

In [18]:
vocab_size = len(dataset.vocabulary)

word_embeddings_final = {}
for index in range(vocab_size):
    word_embeddings_final[dataset.get_index_to_word(index)] = word_embeddings[index]

word_embeddings = word_embeddings_final

In [19]:
word_embeddings

{'<UNK>': array([ 3.29006873e-02, -9.04755816e-02, -2.65045632e-02, -2.25856975e-02,
        -1.16214894e-01, -3.13257575e-02, -2.64157113e-02,  3.88094336e-02,
         1.91144980e-02,  1.01873679e-02,  7.02615157e-02, -6.14453070e-02,
        -1.52079970e-01,  6.47794157e-02, -6.99902028e-02, -4.95540723e-02,
        -1.34107634e-01,  4.59381603e-02, -8.72353017e-02,  4.12183069e-02,
        -2.61653755e-02,  2.38437522e-02, -1.75188154e-01,  2.21003424e-02,
         5.74601479e-02,  2.64663063e-02, -4.31910828e-02, -6.22191466e-02,
         1.63922850e-02, -3.40284333e-02, -1.12691019e-02,  9.77391750e-02,
         1.01151668e-01,  1.40777573e-01, -1.84631739e-02, -7.82908313e-03,
         1.03231575e-02, -6.97100759e-02,  9.23168438e-04, -1.48079684e-03,
         3.89396511e-02, -1.20637223e-01,  3.55775282e-02,  1.47097483e-02,
         6.76514357e-02,  2.18245890e-02,  9.94022191e-02, -2.33385451e-02,
        -1.30520025e-02,  6.62544668e-02,  5.80714410e-03,  5.66067882e-02,
   

### Saving the Embeddings and the Vocabulary

In [20]:
# Save vocabulary to a pickle file
with open('skip-gram-vocabulary.pkl', 'wb') as f:
    pickle.dump(dataset.vocabulary, f)

# Save word embeddings to a pickle file
with open('skip-gram-word-vectors.pkl', 'wb') as f:
    pickle.dump(word_embeddings, f)

torch.save(word_embeddings,"skip-gram-vocabulary.pt")
torch.save(dataset.vocabulary,"skip-gram-word-vectors.pt")

## Training RNN on Word Embeddings

### Extracting the Labels

In [39]:
labels = df["Class Index"][:len(corpus)].values - 1
labels

array([2, 2, 2, ..., 1, 0, 0])

### Generate Sentence Embeddings

In [40]:
def generate_sentence_embeddings(word_embeddings, sentences):
    sentence_embeddings = []
    for sentence in sentences:
        embeddings = [torch.tensor(word_embeddings[word]) for word in sentence if word in word_embeddings]
        if embeddings:
            # Average the embeddings to get the sentence embedding
            sentence_embedding = torch.mean(torch.stack(embeddings), dim=0)
            sentence_embeddings.append(sentence_embedding)
    return torch.stack(sentence_embeddings)

In [41]:
sentence_embeddings = generate_sentence_embeddings(word_embeddings,corpus)
print(np.shape(sentence_embeddings))

torch.Size([39999, 300])


In [43]:
labels = torch.Tensor(labels)
labels.shape

torch.Size([39999])

### Defining the LSTM Model

In [44]:
class LSTMModel(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(LSTMModel, self).__init__()
        self.hidden_size = hidden_size
        self.lstm = nn.LSTM(input_size, hidden_size)
        self.linear1 = nn.Linear(hidden_size, 128)  
        self.linear2 = nn.Linear(128, output_size) 

    def forward(self, x):
        out, _ = self.lstm(x.unsqueeze(1))  
        out = torch.relu(self.linear1(out[:, -1, :]))  
        out = self.linear2(out)
        return out

In [45]:
sentence_embeddings = sentence_embeddings.to(device)
labels = labels.to(device)

### Define Hyperparameters

In [46]:
input_size = sentence_embeddings.size(1) 
hidden_size = 256
output_size = 4  
learning_rate = 0.001
num_epochs = 25

### Create DataLoader

In [47]:
dataset = TensorDataset(sentence_embeddings, labels)
dataset

In [48]:
loader = DataLoader(dataset, batch_size=100, shuffle=True)
loader

### Initialize Model, Loss Function, and Optimizer

In [49]:
model = LSTMModel(input_size, hidden_size, output_size).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)

### Training Loop

In [50]:
for epoch in range(num_epochs):
    running_loss = 0.0
    model.train()  # Set model to training mode
    for inputs, label in tqdm(loader, desc=f'Epoch {epoch + 1}/{num_epochs}', leave=False):                
        label = label.type(torch.LongTensor)
        inputs, label = inputs.to(device), label.to(device)
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, label)
        loss.backward()
        optimizer.step()

        running_loss += loss.item()

    print(f"Epoch {epoch + 1}/{num_epochs}, Loss: {running_loss / len(loader)}")

    # Evaluation on train set
    model.eval()  # Set model to evaluation mode
    train_preds = []
    train_label = []
    for inputs, label in loader:
        inputs, label = inputs.to(device), label.to(device)
        outputs = model(inputs)
        _, predicted = torch.max(outputs, 1)
        train_preds.extend(predicted.tolist())
        train_label.extend(label.tolist())

    train_accuracy = accuracy_score(train_label, train_preds)
    train_f1 = f1_score(train_label, train_preds, average='weighted', zero_division=0)
    train_precision = precision_score(train_label, train_preds, average='weighted', zero_division=0)
    train_recall = recall_score(train_label, train_preds, average='weighted', zero_division=0)
    train_confusion = confusion_matrix(train_label, train_preds)

    print("Train Dataset Metrics:")
    print(f"Accuracy: {train_accuracy}")
    print(f"F1 Score: {train_f1}")
    print(f"Precision: {train_precision}")
    print(f"Recall: {train_recall}")
    print("Confusion Matrix:")
    print(train_confusion)

print("Training complete")

Epoch 1/25, Loss: 0.663850618749857
Train Dataset Metrics:
Accuracy: 0.8187704692617316
F1 Score: 0.8173933949254503
Precision: 0.8225304943955631
Recall: 0.8187704692617316
Confusion Matrix:
[[7893 1112  851  705]
 [ 197 9431   79  190]
 [ 297  375 7114 1591]
 [ 426  553  873 8312]]


Epoch 2/25, Loss: 0.5236777817457914
Train Dataset Metrics:
Accuracy: 0.817870446761169
F1 Score: 0.8185176863573443
Precision: 0.8224176558630509
Recall: 0.817870446761169
Confusion Matrix:
[[9179  429  527  426]
 [1087 8350  109  351]
 [ 825   95 7232 1225]
 [1026  145 1040 7953]]


Epoch 3/25, Loss: 0.4954723051190376
Train Dataset Metrics:
Accuracy: 0.8400710017750443
F1 Score: 0.8398846150141717
Precision: 0.8407644177709297
Recall: 0.8400710017750443
Confusion Matrix:
[[8576  616  654  715]
 [ 312 9202  133  250]
 [ 427  191 7429 1330]
 [ 494  279  996 8395]]


Epoch 4/25, Loss: 0.4842077482491732
Train Dataset Metrics:
Accuracy: 0.8311457786444661
F1 Score: 0.8318645646323527
Precision: 0.8358107395950648
Recall: 0.8311457786444661
Confusion Matrix:
[[8706  472  912  471]
 [ 455 8819  365  258]
 [ 367  107 8019  884]
 [ 649  177 1637 7701]]


Epoch 5/25, Loss: 0.47485834911465646
Train Dataset Metrics:
Accuracy: 0.8431710792769819
F1 Score: 0.8424303307161679
Precision: 0.8431896888401927
Recall: 0.8431710792769819
Confusion Matrix:
[[8721  701  670  469]
 [ 251 9376  131  139]
 [ 444  253 7680 1000]
 [ 601  356 1258 7949]]


...

Epoch 21/25, Loss: 0.3684497325122356
Train Dataset Metrics:
Accuracy: 0.8709467736693417
F1 Score: 0.8700813323697582
Precision: 0.8733122799072368
Recall: 0.8709467736693417
Confusion Matrix:
[[9167  559  304  531]
 [ 191 9477   30  199]
 [ 522  246 7174 1435]
 [ 455  242  448 9019]]


Epoch 22/25, Loss: 0.35696240186691286
Train Dataset Metrics:
Accuracy: 0.8838970974274357
F1 Score: 0.8837627573492234
Precision: 0.8847388665748149
Recall: 0.8838970974274357
Confusion Matrix:
[[9125  451  461  524]
 [ 220 9395   79  203]
 [ 325  143 7816 1093]
 [ 359  213  573 9019]]


Epoch 23/25, Loss: 0.3560157145187259
Train Dataset Metrics:
Accuracy: 0.8856721418035451
F1 Score: 0.8851286902913743
Precision: 0.8855566988648874
Recall: 0.8856721418035451
Confusion Matrix:
[[9253  526  437  345]
 [ 184 9561   58   94]
 [ 323  227 8083  744]
 [ 459  334  842 8529]]


Epoch 24/25, Loss: 0.3454150556027889
Train Dataset Metrics:
Accuracy: 0.8850471261781545
F1 Score: 0.8848572773425559
Precision: 0.8859204953973905
Recall: 0.8850471261781545
Confusion Matrix:
[[9070  500  531  460]
 [ 164 9473   90  170]
 [ 259  146 7863 1109]
 [ 336  225  608 8995]]


Epoch 25/25, Loss: 0.3405021871626377
Train Dataset Metrics:
Accuracy: 0.8903722593064827
F1 Score: 0.8900546313696643
Precision: 0.8915315986504361
Recall: 0.8903722593064827
Confusion Matrix:
[[9244  435  372  510]
 [ 186 9514   55  142]
 [ 321  183 7733 1140]
 [ 318  254  469 9123]]
Training complete


In [59]:
torch.save(model,"skip-gram-classification-model.pt")

## Testing

### Read Data from CSV

In [60]:
testDataPath = "test.csv"
df_test = pd.read_csv(testDataPath)
df_test.head()

Class Index                                        Description
0            3  Unions representing workers at Turner   Newall...
1            4  SPACE.com - TORONTO, Canada -- A second\team o...
2            4  AP - A company founded by a chemistry research...
3            4  AP - It's barely dawn when Mike Fitzpatrick st...
4            4  AP - Southern California's smog-fighting agenc...

In [61]:
corpus_test = df_test["Description"].apply(nltk.word_tokenize)

In [62]:
corpus_test

0       [Unions, representing, workers, at, Turner, Ne...
1       [SPACE.com, -, TORONTO, ,, Canada, --, A, seco...
2       [AP, -, A, company, founded, by, a, chemistry,...
3       [AP, -, It, 's, barely, dawn, when, Mike, Fitz...
4       [AP, -, Southern, California, 's, smog-fightin...
                              ...                        
7595    [Ukrainian, presidential, candidate, Viktor, Y...
7596    [With, the, supply, of, attractive, pitching, ...
7597    [Like, Roger, Clemens, did, almost, exactly, e...
7598    [SINGAPORE, :, Doctors, in, the, United, State...
7599    [EBay, plans, to, buy, the, apartment, and, ho...
Name: Description, Length: 7600, dtype: object

### Extracting the Labels

In [63]:
labels_test = df_test["Class Index"].values - 1
labels_test

array([2, 3, 3, ..., 1, 2, 2])

### Generate Sentence Embeddings

In [64]:
sentence_embeddings_test = generate_sentence_embeddings(word_embeddings,corpus_test)
print(np.shape(sentence_embeddings_test))

torch.Size([7600, 300])


In [65]:
labels_test = torch.Tensor(labels_test)
print(np.shape(labels_test))

torch.Size([7600])


In [66]:
# Convert test data to PyTorch tensors
sentence_embeddings_test = sentence_embeddings_test.to(device)
labels_test = labels_test.to(device)

# Create DataLoader for test data
test_dataset = TensorDataset(sentence_embeddings_test, labels_test)
test_loader = DataLoader(test_dataset, batch_size=100, shuffle=False)

# Evaluation loop
model.eval()  
test_preds = []
test_labels = []

with torch.no_grad(): 
    for inputs, label in test_loader:
        inputs, label = inputs.to(device), label.to(device)
        outputs = model(inputs)
        _, predicted = torch.max(outputs, 1)       
    
        test_preds.extend(predicted.tolist())
        test_labels.extend(label.tolist())

    test_accuracy = accuracy_score(test_labels, test_preds)
    test_f1 = f1_score(test_labels, test_preds, average='weighted')
    test_precision = precision_score(test_labels, test_preds, average='weighted')
    test_recall = recall_score(test_labels, test_preds, average='weighted')
    test_confusion = confusion_matrix(test_labels, test_preds)

    print("Test Dataset Metrics:")
    print(f"Accuracy: {test_accuracy}")
    print(f"F1 Score: {test_f1}")
    print(f"Precision: {test_precision}")
    print(f"Recall: {test_recall}")
    print("Confusion Matrix:")
    print(test_confusion)

Test Dataset Metrics:
Accuracy: 0.8398684210526316
F1 Score: 0.839065590449206
Precision: 0.840891304604194
Recall: 0.8398684210526316
Confusion Matrix:
[[1592   86  100  122]
 [  48 1792   29   31]
 [ 104   57 1412  327]
 [  81   82  150 1587]]
